In [56]:
from sklearn import preprocessing
import os
import sys
import matplotlib.pyplot as plt

csv= pd.read_csv('/Users/shenghaoisyummy/Capstone/filted_brief.csv', index_col=0)
csv = csv.rename(columns={'station_arrival_status': 'actual_station_arrv_time'})
csv = csv.dropna()

In [59]:
feature_extraction_data = csv
feature_extraction_data.info()
from datetime import datetime, timedelta
import pandas as pd
import numpy as np

def change_date_format(df):
    for idx, row in df.iterrows():
        row_date = datetime.strptime(row['service_date'], '%d/%m/%Y')
        row_date_str = datetime.strftime(row_date, '%d/%m/%Y')
        df.loc[idx, 'service_date'] = row_date_str

def __datetime(date_str):
    return datetime.strptime(date_str, "%d/%m/%Y %H:%M")

def cal_late_time(df):
    for idx, row in df.iterrows():
        planned_dprt_time = __datetime(str(row['planned_station_dprt_time']))
        actual_dprt_time = __datetime(str(row['actual_station_dprt_time']))
        planned_arrv_time = __datetime(str(row['planned_station_arrv_time']))
        actual_arrv_time = __datetime(str(row['actual_station_arrv_time']))
        delta_arrv = actual_arrv_time - planned_arrv_time
        delta_dprt = actual_dprt_time - planned_dprt_time
        df.loc[idx,'arrv_late_time'] = delta_arrv.total_seconds()
        df.loc[idx,'dprt_late_time'] = delta_dprt.total_seconds()
        print("Currently on row: {}; Currently iterrated {}% of rows".format(idx, (idx + 1)/len(df.index) * 100))


def cal_last_node_late(df):
    for idx, row in df.iloc[1:].iterrows():
        last_node_row = df.loc[(df['service_date'] == row['service_date']) & (df['trip_name'] == row['trip_name']) & (df['node_seq_order'] == row['node_seq_order'] - 1)]
        if last_node_row.empty:
            df.loc[idx, 'last_node_arrv_late_time'] = 0
            df.loc[idx, 'last_node_dprt_late_time'] = 0
        else:
            last_node_arrv_late_time = last_node_row.arrv_late_time.values
            last_node_dprt_late_time = last_node_row.dprt_late_time.values
            df.loc[idx, 'last_node_arrv_late_time'] = last_node_arrv_late_time
            df.loc[idx, 'last_node_dprt_late_time'] = last_node_dprt_late_time
        print("Currently on row: {}; Currently iterrated {}% of rows".format(idx, (idx + 1)/len(df.index) * 100))

def cal_last_n_node_late(df, n):
    for idx, row in df.iterrows():
        arrv_late_time_array = []
        dprt_late_time_array = []
        if row['node_seq_order'] > n:
            for i in range(1, n + 1):
                last_n_node_row = df.loc[(df['service_date'] == row['service_date']) & (df['trip_name'] == row['trip_name']) & (df['node_seq_order'] == row['node_seq_order'] - i)]
                if last_n_node_row.empty:
                    arrv_late_time_array.append(0)
                    dprt_late_time_array.append(0)
                else:
                    arrv_late_time_array.append(last_n_node_row.arrv_late_time.values)
                    dprt_late_time_array.append(last_n_node_row.dprt_late_time.values)
            df.loc[idx, 'last_{}_node_arrv_late_time_sum'.format(n)] = np.sum(arrv_late_time_array)
            df.loc[idx, 'last_{}_node_dprt_late_time_sum'.format(n)] = np.sum(dprt_late_time_array)
            df.loc[idx, 'last_{}_node_arrv_late_time_mean'.format(n)] = np.mean(arrv_late_time_array)
            df.loc[idx, 'last_{}_node_dprt_late_time_mean'.format(n)] = np.mean(dprt_late_time_array)
            df.loc[idx, 'last_{}_node_arrv_late_time_median'.format(n)] = np.median(arrv_late_time_array)
            df.loc[idx, 'last_{}_node_dprt_late_time_median'.format(n)] = np.median(dprt_late_time_array)
            df.loc[idx, 'last_{}_node_arrv_late_time_std'.format(n)] = np.std(arrv_late_time_array)
            df.loc[idx, 'last_{}_node_dprt_late_time_std'.format(n)] = np.std(dprt_late_time_array)
            df.loc[idx, 'last_{}_node_arrv_late_time_max'.format(n)] = np.max(arrv_late_time_array)
            df.loc[idx, 'last_{}_node_dprt_late_time_max'.format(n)] = np.max(dprt_late_time_array)
            df.loc[idx, 'last_{}_node_arrv_late_time_min'.format(n)] = np.min(arrv_late_time_array)
            df.loc[idx, 'last_{}_node_dprt_late_time_min'.format(n)] = np.min(dprt_late_time_array)
        else:
            df.loc[idx, 'last_{}_node_arrv_late_time_sum'.format(n)] = 0
            df.loc[idx, 'last_{}_node_dprt_late_time_sum'.format(n)] = 0
            df.loc[idx, 'last_{}_node_arrv_late_time_mean'.format(n)] = 0
            df.loc[idx, 'last_{}_node_dprt_late_time_mean'.format(n)] = 0
            df.loc[idx, 'last_{}_node_arrv_late_time_median'.format(n)] = 0
            df.loc[idx, 'last_{}_node_dprt_late_time_median'.format(n)] = 0
            df.loc[idx, 'last_{}_node_arrv_late_time_std'.format(n)] = 0
            df.loc[idx, 'last_{}_node_dprt_late_time_std'.format(n)] = 0
            df.loc[idx, 'last_{}_node_arrv_late_time_max'.format(n)] = 0
            df.loc[idx, 'last_{}_node_dprt_late_time_max'.format(n)] = 0
            df.loc[idx, 'last_{}_node_arrv_late_time_min'.format(n)] = 0
            df.loc[idx, 'last_{}_node_dprt_late_time_min'.format(n)] = 0
        print("Currently on row: {}; Currently iterrated {}% of rows".format(idx, (idx + 1)/len(df.index) * 100))
        
def rowelement(colname, df):
    list = []
    for index, row in df.iterrows():
        if row[colname] not in list:
            list.append(row[colname])
    return list

def col_group(df, group_col_str):
    df_describe_arrv = df.groupby(group_col_str).arrv_late_time.mean().describe().values
    df_describe_dprt = df.groupby(group_col_str).dprt_late_time.mean().describe().values
    for idx, row in df.iterrows():
        if row['arrv_late_time'] < df_describe_arrv[4]:
            df.loc[idx,'{}_arrv_group'.format(group_col_str)] = 'less_than_.25'
        if df_describe_arrv[4] < row['arrv_late_time'] < df_describe_arrv[5]:
            df.loc[idx,'{}_arrv_group'.format(group_col_str)] = '.25_to_.50'
        if df_describe_arrv[5] < row['arrv_late_time'] < df_describe_arrv[6]:
            df.loc[idx,'{}_arrv_group'.format(group_col_str)] = '.50_to_.75'
        if df_describe_arrv[6] < row['arrv_late_time']:
            df.loc[idx,'{}_arrv_group'.format(group_col_str)] = 'great_than_.75'
            
        if row['dprt_late_time'] < df_describe_dprt[4]:
            df.loc[idx,'{}_dprt_group'.format(group_col_str)] = 'less_than_.25'
        if df_describe_dprt[4] < row['dprt_late_time'] < df_describe_dprt[5]:
            df.loc[idx,'{}_dprt_group'.format(group_col_str)] = '.25_to_.50'
        if df_describe_dprt[5] < row['dprt_late_time'] < df_describe_dprt[6]:
            df.loc[idx,'{}_dprt_group'.format(group_col_str)] = '.50_to_.75'
        if df_describe_dprt[6] < row['dprt_late_time']:
            df.loc[idx,'{}_dprt_group'.format(group_col_str)] = 'great_than_.75'
        print("Currently on row: {}; Currently iterrated {}% of rows".format(idx, (idx + 1)/len(df.index) * 100))

def cal_last_n_days_late(df, n):
    df_start_date_str = df.loc[1]['service_date']
    df_start_date = datetime.strptime(df_start_date_str, '%d/%m/%Y')
    loop_start_date_str = datetime.strftime(df_start_date + timedelta(n), '%d/%m/%Y')
    for idx, row in df.iterrows():
        arrv_late_time_array = []
        dprt_late_time_array = []
        row_service_date = datetime.strptime(row['service_date'], '%d/%m/%Y')
        loop_start_date = datetime.strptime(loop_start_date_str, '%d/%m/%Y')
        if row_service_date >= loop_start_date:
            for i in range(1, n + 1):
                pre_n_service_date_str = datetime.strftime(row_service_date - timedelta(i), '%d/%m/%Y')
                last_n_days_rows = df.loc[(df['service_date'] == pre_n_service_date_str) & (df['actual_stop_node'] == row['actual_stop_node'])]
                for index, last_n_days_row in last_n_days_rows.iterrows():
                    if last_n_days_row.empty:
                        arrv_late_time_array.append(0)
                        dprt_late_time_array.append(0)
                    else:
                        arrv_late_time_array.append(last_n_days_row['arrv_late_time'])
                        dprt_late_time_array.append(last_n_days_row['dprt_late_time'])
            if(all(v == 0 for v in  dprt_late_time_array) == False):
                df.loc[idx, 'last_{}_days_arrv_late_time_sum'.format(n)] = np.sum(arrv_late_time_array)
                df.loc[idx, 'last_{}_days_dprt_late_time_sum'.format(n)] = np.sum(dprt_late_time_array)
                df.loc[idx, 'last_{}_days_arrv_late_time_mean'.format(n)] = np.mean(arrv_late_time_array)
                df.loc[idx, 'last_{}_days_dprt_late_time_mean'.format(n)] = np.mean(dprt_late_time_array)
                df.loc[idx, 'last_{}_days_arrv_late_time_median'.format(n)] = np.median(arrv_late_time_array)
                df.loc[idx, 'last_{}_days_dprt_late_time_median'.format(n)] = np.median(dprt_late_time_array)
                df.loc[idx, 'last_{}_days_arrv_late_time_std'.format(n)] = np.std(arrv_late_time_array)
                df.loc[idx, 'last_{}_days_dprt_late_time_std'.format(n)] = np.std(dprt_late_time_array)
                df.loc[idx, 'last_{}_days_arrv_late_time_max'.format(n)] = np.max(arrv_late_time_array)
                df.loc[idx, 'last_{}_days_dprt_late_time_max'.format(n)] = np.max(dprt_late_time_array)
                df.loc[idx, 'last_{}_days_arrv_late_time_min'.format(n)] = np.min(arrv_late_time_array)
                df.loc[idx, 'last_{}_days_dprt_late_time_min'.format(n)] = np.min(dprt_late_time_array)
            else:
                df.loc[idx, 'last_{}_days_arrv_late_time_sum'.format(n)] = 0
                df.loc[idx, 'last_{}_days_dprt_late_time_sum'.format(n)] = 0
                df.loc[idx, 'last_{}_days_arrv_late_time_mean'.format(n)] = 0
                df.loc[idx, 'last_{}_days_dprt_late_time_mean'.format(n)] = 0
                df.loc[idx, 'last_{}_days_arrv_late_time_median'.format(n)] = 0
                df.loc[idx, 'last_{}_days_dprt_late_time_median'.format(n)] = 0
                df.loc[idx, 'last_{}_days_arrv_late_time_std'.format(n)] = 0
                df.loc[idx, 'last_{}_days_dprt_late_time_std'.format(n)] = 0
                df.loc[idx, 'last_{}_days_arrv_late_time_max'.format(n)] = 0
                df.loc[idx, 'last_{}_days_dprt_late_time_max'.format(n)] = 0
                df.loc[idx, 'last_{}_days_arrv_late_time_min'.format(n)] = 0
                df.loc[idx, 'last_{}_days_dprt_late_time_min'.format(n)] = 0
        else:
            df.loc[idx, 'last_{}_days_arrv_late_time_sum'.format(n)] = 0
            df.loc[idx, 'last_{}_days_dprt_late_time_sum'.format(n)] = 0
            df.loc[idx, 'last_{}_days_arrv_late_time_mean'.format(n)] = 0
            df.loc[idx, 'last_{}_days_dprt_late_time_mean'.format(n)] = 0
            df.loc[idx, 'last_{}_days_arrv_late_time_median'.format(n)] = 0
            df.loc[idx, 'last_{}_days_dprt_late_time_median'.format(n)] = 0
            df.loc[idx, 'last_{}_days_arrv_late_time_std'.format(n)] = 0
            df.loc[idx, 'last_{}_days_dprt_late_time_std'.format(n)] = 0
            df.loc[idx, 'last_{}_days_arrv_late_time_max'.format(n)] = 0
            df.loc[idx, 'last_{}_days_dprt_late_time_max'.format(n)] = 0
            df.loc[idx, 'last_{}_days_arrv_late_time_min'.format(n)] = 0
            df.loc[idx, 'last_{}_days_dprt_late_time_min'.format(n)] = 0
        print("Currently on row: {}; Currently iterrated {}% of rows".format(idx, (idx + 1)/len(df.index) * 100))

def is_same_stop_station(df):
    df['is_same_stop_node'] = np.where(df['planned_stop_node'] == df['actual_stop_node'] , 1, 0)
    df['is_same_stop_station'] = np.where(df['planned_stop_station'] == df['actual_stop_station'] , 1, 0)

def date_to_week(df):
    datetime = pd.to_datetime(df['service_date'], format='%d/%m/%Y')
    df['day_of_week'] = datetime.dt.dayofweek
    df['is_weekend'] = np.where((test['day_of_week'] == 5) | (test['day_of_week'] == 6) , 1, 0)


def split_date(df, col_str):
    datetime = pd.to_datetime(df[col_str], format="%d/%m/%Y %H:%M")
    df['{}_year'.format(col_str)] = datetime.dt.strftime('%Y').apply(int)
    df['{}_month'.format(col_str)] = datetime.dt.strftime('%-m').apply(int)
    df['{}_days'.format(col_str)] = datetime.dt.strftime('%-d').apply(int)
    df['{}_hours'.format(col_str)] = datetime.dt.strftime('%-H').apply(int)
    df['{}_minutes'.format(col_str)] = datetime.dt.strftime('%-M').apply(int)

def is_peak_time(df):
    df['is_peak_time'] = np.where(((6 <= df['actual_arrv_hours']) & (df['actual_arrv_hours'] <= 8)) | ((16 <= df['actual_arrv_hours'])& ( df['actual_arrv_hours']<= 19)), 1, 0)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 17954 entries, 0 to 97424
Data columns (total 19 columns):
business_centre              17954 non-null object
service_date                 17954 non-null object
segment_direction            17954 non-null object
trip_name                    17954 non-null object
service_line                 17954 non-null object
origin_station               17954 non-null object
dest_station                 17954 non-null object
trip_dprt_status             17954 non-null object
trip_arrv_status             17954 non-null object
leading_set_number           17954 non-null object
node_seq_order               17954 non-null int64
planned_stop_node            17954 non-null object
planned_stop_station         17954 non-null object
planned_station_dprt_time    17954 non-null object
planned_station_arrv_time    17954 non-null object
actual_stop_node             17954 non-null object
actual_stop_station          17954 non-null object
actual_station_dprt_time 

In [ ]:
change_date_format(feature_extraction_data)
cal_late_time(feature_extraction_data)
cal_last_node_late(feature_extraction_data)
cal_last_n_node_late(feature_extraction_data, 2)
cal_last_n_node_late(feature_extraction_data, 7 )
cal_last_n_node_late(feature_extraction_data, 14)
cal_last_n_days_late(feature_extraction_data, 2)
cal_last_n_days_late(feature_extraction_data, 7)
cal_last_n_days_late(feature_extraction_data, 14)
col_group(feature_extraction_data, 'trip_name')
col_group(feature_extraction_data, 'leading_set_number')
col_group(feature_extraction_data, 'trip_name')
col_group(feature_extraction_data, 'planned_stop_node')
col_group(feature_extraction_data, 'actual_stop_node')
is_same_stop_station(feature_extraction_data)
date_to_week(feature_extraction_data)
split_date(feature_extraction_data, 'planned_station_dprt_time')
split_date(feature_extraction_data, 'planned_station_arrv_time')
split_date(feature_extraction_data, 'actual_station_dprt_time')
split_date(feature_extraction_data, 'actual_station_dprt_time')
is_peak_time(feature_extraction_data)

Currently on row: 0; Currently iterrated 0.005569789461958338% of rows
Currently on row: 1; Currently iterrated 0.011139578923916676% of rows
Currently on row: 2; Currently iterrated 0.016709368385875015% of rows
Currently on row: 3; Currently iterrated 0.022279157847833353% of rows
Currently on row: 4; Currently iterrated 0.027848947309791688% of rows
Currently on row: 5; Currently iterrated 0.03341873677175003% of rows
Currently on row: 6; Currently iterrated 0.03898852623370837% of rows
Currently on row: 7; Currently iterrated 0.044558315695666706% of rows
Currently on row: 8; Currently iterrated 0.050128105157625044% of rows
Currently on row: 9; Currently iterrated 0.055697894619583375% of rows
Currently on row: 10; Currently iterrated 0.06126768408154172% of rows
Currently on row: 11; Currently iterrated 0.06683747354350006% of rows
Currently on row: 12; Currently iterrated 0.07240726300545838% of rows
Currently on row: 13; Currently iterrated 0.07797705246741674% of rows
Currentl

Currently on row: 158; Currently iterrated 0.8855965244513757% of rows
Currently on row: 159; Currently iterrated 0.891166313913334% of rows
Currently on row: 160; Currently iterrated 0.8967361033752924% of rows
Currently on row: 161; Currently iterrated 0.9023058928372508% of rows
Currently on row: 162; Currently iterrated 0.9078756822992091% of rows
Currently on row: 163; Currently iterrated 0.9134454717611675% of rows
Currently on row: 164; Currently iterrated 0.9190152612231257% of rows
Currently on row: 165; Currently iterrated 0.9245850506850841% of rows
Currently on row: 166; Currently iterrated 0.9301548401470424% of rows
Currently on row: 168; Currently iterrated 0.9412944190709591% of rows
Currently on row: 169; Currently iterrated 0.9468642085329175% of rows
Currently on row: 170; Currently iterrated 0.9524339979948757% of rows
Currently on row: 171; Currently iterrated 0.9580037874568341% of rows
Currently on row: 172; Currently iterrated 0.9635735769187924% of rows
Current

Currently on row: 289; Currently iterrated 1.6152389439679182% of rows
Currently on row: 290; Currently iterrated 1.6208087334298762% of rows
Currently on row: 291; Currently iterrated 1.6263785228918346% of rows
Currently on row: 292; Currently iterrated 1.631948312353793% of rows
Currently on row: 293; Currently iterrated 1.6375181018157512% of rows
Currently on row: 294; Currently iterrated 1.6430878912777096% of rows
Currently on row: 295; Currently iterrated 1.648657680739668% of rows
Currently on row: 296; Currently iterrated 1.6542274702016264% of rows
Currently on row: 297; Currently iterrated 1.6597972596635848% of rows
Currently on row: 298; Currently iterrated 1.665367049125543% of rows
Currently on row: 299; Currently iterrated 1.6709368385875014% of rows
Currently on row: 300; Currently iterrated 1.6765066280494598% of rows
Currently on row: 301; Currently iterrated 1.6820764175114182% of rows
Currently on row: 302; Currently iterrated 1.6876462069733766% of rows
Currently

Currently on row: 446; Currently iterrated 2.489695889495377% of rows
Currently on row: 447; Currently iterrated 2.4952656789573355% of rows
Currently on row: 448; Currently iterrated 2.500835468419294% of rows
Currently on row: 449; Currently iterrated 2.5064052578812523% of rows
Currently on row: 450; Currently iterrated 2.5119750473432108% of rows
Currently on row: 451; Currently iterrated 2.5175448368051687% of rows
Currently on row: 452; Currently iterrated 2.523114626267127% of rows
Currently on row: 453; Currently iterrated 2.5286844157290855% of rows
Currently on row: 454; Currently iterrated 2.5342542051910435% of rows
Currently on row: 455; Currently iterrated 2.539823994653002% of rows
Currently on row: 456; Currently iterrated 2.5453937841149603% of rows
Currently on row: 457; Currently iterrated 2.5509635735769187% of rows
Currently on row: 458; Currently iterrated 2.556533363038877% of rows
Currently on row: 459; Currently iterrated 2.5621031525008355% of rows
Currently o

Currently on row: 604; Currently iterrated 3.3697226244847944% of rows
Currently on row: 605; Currently iterrated 3.3752924139467533% of rows
Currently on row: 606; Currently iterrated 3.3808622034087112% of rows
Currently on row: 607; Currently iterrated 3.386431992870669% of rows
Currently on row: 608; Currently iterrated 3.392001782332628% of rows
Currently on row: 609; Currently iterrated 3.397571571794586% of rows
Currently on row: 610; Currently iterrated 3.4031413612565444% of rows
Currently on row: 611; Currently iterrated 3.408711150718503% of rows
Currently on row: 612; Currently iterrated 3.4142809401804612% of rows
Currently on row: 613; Currently iterrated 3.419850729642419% of rows
Currently on row: 614; Currently iterrated 3.425420519104378% of rows
Currently on row: 615; Currently iterrated 3.430990308566336% of rows
Currently on row: 616; Currently iterrated 3.436560098028295% of rows
Currently on row: 617; Currently iterrated 3.442129887490253% of rows
Currently on ro

...

Currently on row: 95768; Currently iterrated 533.4131669822881% of rows
Currently on row: 95769; Currently iterrated 533.41873677175% of rows
Currently on row: 95770; Currently iterrated 533.424306561212% of rows
Currently on row: 95771; Currently iterrated 533.4298763506739% of rows
Currently on row: 95772; Currently iterrated 533.4354461401359% of rows
Currently on row: 95773; Currently iterrated 533.4410159295978% of rows
Currently on row: 95774; Currently iterrated 533.4465857190598% of rows
Currently on row: 95775; Currently iterrated 533.4521555085217% of rows
Currently on row: 95776; Currently iterrated 533.4577252979838% of rows
Currently on row: 95777; Currently iterrated 533.4632950874457% of rows
Currently on row: 95778; Currently iterrated 533.4688648769077% of rows
Currently on row: 95779; Currently iterrated 533.4744346663696% of rows
Currently on row: 95780; Currently iterrated 533.4800044558316% of rows
Currently on row: 95781; Currently iterrated 533.4855742452936% of 

Currently on row: 95885; Currently iterrated 534.0648323493373% of rows
Currently on row: 95886; Currently iterrated 534.0704021387992% of rows
Currently on row: 95887; Currently iterrated 534.0759719282612% of rows
Currently on row: 95888; Currently iterrated 534.0815417177231% of rows
Currently on row: 95889; Currently iterrated 534.0871115071851% of rows
Currently on row: 95890; Currently iterrated 534.092681296647% of rows
Currently on row: 95891; Currently iterrated 534.098251086109% of rows
Currently on row: 95892; Currently iterrated 534.1038208755709% of rows
Currently on row: 95893; Currently iterrated 534.1093906650328% of rows
Currently on row: 95894; Currently iterrated 534.1149604544948% of rows
Currently on row: 95895; Currently iterrated 534.1205302439568% of rows
Currently on row: 95896; Currently iterrated 534.1261000334188% of rows
Currently on row: 95897; Currently iterrated 534.1316698228807% of rows
Currently on row: 95898; Currently iterrated 534.1372396123427% of

Currently on row: 96001; Currently iterrated 534.7109279269243% of rows
Currently on row: 96002; Currently iterrated 534.7164977163862% of rows
Currently on row: 96003; Currently iterrated 534.7220675058483% of rows
Currently on row: 96004; Currently iterrated 534.7276372953102% of rows
Currently on row: 96005; Currently iterrated 534.7332070847722% of rows
Currently on row: 96006; Currently iterrated 534.7387768742341% of rows
Currently on row: 96007; Currently iterrated 534.7443466636961% of rows
Currently on row: 96008; Currently iterrated 534.749916453158% of rows
Currently on row: 96009; Currently iterrated 534.75548624262% of rows
Currently on row: 96010; Currently iterrated 534.7610560320819% of rows
Currently on row: 96011; Currently iterrated 534.7666258215439% of rows
Currently on row: 96012; Currently iterrated 534.7721956110058% of rows
Currently on row: 96013; Currently iterrated 534.7777654004678% of rows
Currently on row: 96014; Currently iterrated 534.7833351899299% of 

Currently on row: 96128; Currently iterrated 535.4182911885931% of rows
Currently on row: 96129; Currently iterrated 535.423860978055% of rows
Currently on row: 96130; Currently iterrated 535.429430767517% of rows
Currently on row: 96131; Currently iterrated 535.4350005569789% of rows
Currently on row: 96132; Currently iterrated 535.440570346441% of rows
Currently on row: 96133; Currently iterrated 535.4461401359029% of rows
Currently on row: 96134; Currently iterrated 535.4517099253649% of rows
Currently on row: 96135; Currently iterrated 535.4572797148268% of rows
Currently on row: 96137; Currently iterrated 535.4684192937507% of rows
Currently on row: 96138; Currently iterrated 535.4739890832127% of rows
Currently on row: 96139; Currently iterrated 535.4795588726746% of rows
Currently on row: 96140; Currently iterrated 535.4851286621366% of rows
Currently on row: 96141; Currently iterrated 535.4906984515985% of rows
Currently on row: 96142; Currently iterrated 535.4962682410605% of 

Currently on row: 96243; Currently iterrated 536.0588169767183% of rows
Currently on row: 96244; Currently iterrated 536.0643867661803% of rows
Currently on row: 96245; Currently iterrated 536.0699565556422% of rows
Currently on row: 96246; Currently iterrated 536.0755263451042% of rows
Currently on row: 96247; Currently iterrated 536.0810961345661% of rows
Currently on row: 96248; Currently iterrated 536.0866659240281% of rows
Currently on row: 96250; Currently iterrated 536.097805502952% of rows
Currently on row: 96251; Currently iterrated 536.103375292414% of rows
Currently on row: 96252; Currently iterrated 536.1089450818758% of rows
Currently on row: 96253; Currently iterrated 536.1145148713379% of rows
Currently on row: 96254; Currently iterrated 536.1200846607998% of rows
Currently on row: 96255; Currently iterrated 536.1256544502618% of rows
Currently on row: 96256; Currently iterrated 536.1312242397237% of rows
Currently on row: 96257; Currently iterrated 536.1367940291857% of

In [52]:
feature_extraction_data.info()

['/Users/shenghaoisyummy/Capstone/Predicting-train-arrv-time/helperfunction',
 '/Users/shenghaoisyummy/Capstone/Predicting-train-arrv-time/helperfunction',
 '/Users/shenghaoisyummy/Capstone/Predicting-train-arrv-time/helperfunction',
 '/Users/shenghaoisyummy/Capstone/Predicting-train-arrv-time/helperfunction',
 '/Users/shenghaoisyummy/Capstone/Predicting-train-arrv-time/helperfunction',
 '/Users/shenghaoisyummy/Capstone/Predicting-train-arrv-time/helperfunction',
 '/Users/shenghaoisyummy/Capstone/Predicting-train-arrv-time/helperfunction',
 '/Users/shenghaoisyummy/Capstone/Predicting-train-arrv-time/helperfunction',
 '/Users/shenghaoisyummy/Capstone/Predicting-train-arrv-time/helperfunction',
 '/Users/shenghaoisyummy/Capstone/Predicting-train-arrv-time/helperfunction',
 '/Users/shenghaoisyummy/Capstone/Predicting-train-arrv-time/helperfunction',
 '/Users/shenghaoisyummy/Capstone/Predicting-train-arrv-time/helperfunction',
 '/Users/shenghaoisyummy/Capstone/Predicting-train-arrv-time/hel